# Disable contracts (for performance)

In [1]:
import os
# os.environ["DISABLE_CONTRACTS"] = "true"

# Importing necessary modules

In [2]:
from tqdm import tqdm_notebook as tqdm
from joblib import Parallel, delayed
import itertools

In [3]:
import numpy as np

In [4]:
from osol.extremum.optimization.basic.vector import Vector
from osol.extremum.optimization.tasks.fmu_program_control import FMUProgramControl

from osol.extremum.optimization.algorithms.random_search import RandomSearch
from osol.extremum.optimization.algorithms.statistical_anti_gradient_random_search import StatisticalAntiGradientRandomSearch


from osol.extremum.optimization.basic.terminator import MaxTimeTerminator

In [5]:
import plotly.offline as py
import plotly.graph_objs as go

py.init_notebook_mode(connected=True)

# Task Description

Task is to orient spacecraft with desired values

# a*x + b

In [6]:
-12*np.pi, 6 * np.pi

(-37.69911184307752, 18.84955592153876)

# Problem initialization

In [7]:
model = FMUProgramControl(source_dir="./models_fmu/spacecraft_with_linear_controller/")

Compiling spacecraft.dylib...
/var/folders/d_/2kzh_1ks41d7tgrmt7fnp8pc0000gn/T/tmpad_ox8f1/sources
gcc -c -I. -I/Users/wol4aravio/.local/share/virtualenvs/OSOL.Extremum_Applications-PIcyG7GX/lib/python3.6/site-packages/fmpy/c-code/fmi2 -DCO_SIMULATION -DFMI2_FUNCTION_PREFIX=spacecraft_ spacecraft.c /Users/wol4aravio/.local/share/virtualenvs/OSOL.Extremum_Applications-PIcyG7GX/lib/python3.6/site-packages/fmpy/c-code/fmi2/fmi2_wrapper.c && gcc -shared -ospacecraft.dylib *.o


In [8]:
search_area = {
    "a": (-100.0, 100.0),
    "b": (-100.0, 100.0)
}

inits = {"x1_0": 0.0, "x2_0": 0.0}

In [9]:
def criterion(v):
    sim_results = model.simulate(initial_state=inits, parameters=v.to_dict())
    return model.get_criterion_value(sim_results)

def get_criterion_value(a, b):
    values = criterion(Vector.create(a=a, b=b))
    return [values["I"], values["x1_penalty"], values["x2_penalty"]]

def f(v):
    values = criterion(v)
    return np.log(np.sum(list(values.values())))

In [10]:
N = 200

a_values = np.linspace(*search_area["a"], num=(N + 1))
b_values = np.linspace(*search_area["b"], num=(N + 1))
ab_comb = list(itertools.product(a_values, b_values))

criterion_values = np.zeros(shape=[N+1, N+1, 3])

values = Parallel(n_jobs=-1)(delayed(get_criterion_value)(a=a, b=b) for a, b in tqdm(ab_comb))
k = 0
for j, _ in enumerate(b_values):
    for i, _ in enumerate(a_values):
        criterion_values[i, j, ] = values[k]
        k += 1

In [11]:
plot_contour = go.Contour(
    z=np.log(criterion_values.sum(axis=2)),
    x=a_values,
    y=b_values)

In [12]:
data = [plot_contour]

layout = go.Layout(
    title="Log(Criterion value)",
    width=1000,
    height=1000,
    xaxis={
        "title": "`a` coefficient",
    },
    yaxis={
        "title": "`b` coefficient",
    },
)

figure = go.Figure(data, layout)
py.iplot(figure)

# Algorithm initialization and application

In [13]:
points = []

def save_point(a, s):
    points.append(s["x"])

In [14]:
# algorithm = RandomSearch(radius=2.5)

algorithm = StatisticalAntiGradientRandomSearch(radius=2.5, number_of_samples=10)

In [15]:
f_term = MaxTimeTerminator(f=f, mode="dummy", max_time="m:10")

In [16]:
optimal = algorithm.optimize(f_term, search_area, callbacks=[save_point])

In [17]:
optimal

a -> -37.596649169921875, b -> 18.784746170043945

In [18]:
sim_res = model.simulate(inits, optimal.to_dict())

sim_res["x1"][-1], sim_res["x2"][-1]

(3.135658309318533, 0.005219909667954298)

In [19]:
get_criterion_value(**optimal)

[117.79224518897027, 0.005934344271260272, 0.005219909667954298]

In [20]:
plot_line = go.Scatter(
    x = [p["a"] for p in points],
    y = [p["b"] for p in points],
#     mode = 'markers',
    marker = dict(
        size = 3,
        color = 'rgba(0, 255, 0, .5)',
        line = dict(width = 1, color = 'rgb(0, 0, 0)')))

plot_scatter = go.Scatter(
    x = [p["a"] for p in points],
    y = [p["b"] for p in points],
    mode = 'markers',
    marker = dict(
        size = 3,
        color = 'rgba(0, 255, 0, .5)',
        line = dict(width = 1, color = 'rgb(0, 0, 0)')))

data = [plot_contour, plot_line, plot_scatter]

layout = go.Layout(
    title="History",
    width=1000,
    height=1000,
    xaxis={
        "title": "`a` coefficient",
    },
    yaxis={
        "title": "`b` coefficient",
    },
)

figure = go.Figure(data, layout)
py.iplot(figure)

# Removal of temp files

In [24]:
model.purge()